In [0]:
# Import necessary PySpark SQL functions and Window functionality
# - col: For column references and operations
# - year, current_date: For date manipulations
# - avg, min, max, count: Aggregate functions for statistical analysis
# - when: For conditional logic (similar to IF-THEN-ELSE)
# - rank, dense_rank: Window functions for ranking results
# - Window: For defining partitioning and ordering in window operations
from pyspark.sql.functions import col, year, current_date, avg, min, max, count, when, rank, dense_rank, lit, concat, datediff, substring, upper, stddev, sum
from pyspark.sql.window import Window
from pyspark.sql.types import IntegerType, DateType

In [0]:
#Read in the two datasets that are necesary for this take home assignment
df_laptimes = spark.read.csv('s3://columbia-gr5069-main/raw/lap_times.csv', header=True)
df_drivers = spark.read.csv('s3://columbia-gr5069-main/raw/drivers.csv', header=True)
df_races = spark.read.csv('s3://columbia-gr5069-main/raw/races.csv', header=True)
df_results = spark.read.csv('s3://columbia-gr5069-main/raw/results.csv', header=True)
df_pit_stops = spark.read.csv('s3://columbia-gr5069-main/raw/pit_stops.csv', header=True)
df_status = spark.read.csv('s3://columbia-gr5069-main/raw/status.csv', header=True)
df_qualifying = spark.read.csv("s3://columbia-gr5069-main/raw/qualifying.csv", header=True, inferSchema=True)



In [0]:
#Observing each table 

print("Lap Times Schema:")
df_laptimes.printSchema()

print("Drivers Schema:")
df_drivers.printSchema()

print("Races Schema:")
df_races.printSchema()

print("Results Schema:")
df_results.printSchema()

print("Pit Stops Schema:")
df_pit_stops.printSchema()

print("Status Schema:")
df_status.printSchema()

print("Qualifying Schema:")
df_qualifying.printSchema()

# Display a sample of each dataset
display(df_laptimes.limit(3))
display(df_drivers.limit(3))
display(df_races.limit(3))
display(df_results.limit(3))
display(df_pit_stops.limit(3))
display(df_status.limit(3))
display(df_qualifying.limit(3))

Lap Times Schema:
root
 |-- raceId: string (nullable = true)
 |-- driverId: string (nullable = true)
 |-- lap: string (nullable = true)
 |-- position: string (nullable = true)
 |-- time: string (nullable = true)
 |-- milliseconds: string (nullable = true)

Drivers Schema:
root
 |-- driverId: string (nullable = true)
 |-- driverRef: string (nullable = true)
 |-- number: string (nullable = true)
 |-- code: string (nullable = true)
 |-- forename: string (nullable = true)
 |-- surname: string (nullable = true)
 |-- dob: string (nullable = true)
 |-- nationality: string (nullable = true)
 |-- url: string (nullable = true)

Races Schema:
root
 |-- raceId: string (nullable = true)
 |-- year: string (nullable = true)
 |-- round: string (nullable = true)
 |-- circuitId: string (nullable = true)
 |-- name: string (nullable = true)
 |-- date: string (nullable = true)
 |-- time: string (nullable = true)
 |-- url: string (nullable = true)
 |-- fp1_date: string (nullable = true)
 |-- fp1_time: strin

raceId driverId lap position time milliseconds 841 20 1 1 1:38.109 98109 841 20 2 1 1:33.006 93006 841 20 3 1 1:32.713 92713

driverId driverRef number code forename surname dob nationality url 1 hamilton 44 HAM Lewis Hamilton 1985-01-07 British http://en.wikipedia.org/wiki/Lewis_Hamilton 2 heidfeld \N HEI Nick Heidfeld 1977-05-10 German http://en.wikipedia.org/wiki/Nick_Heidfeld 3 rosberg 6 ROS Nico Rosberg 1985-06-27 German http://en.wikipedia.org/wiki/Nico_Rosberg

raceId year round circuitId name date time url fp1_date fp1_time fp2_date fp2_time fp3_date fp3_time quali_date quali_time sprint_date sprint_time 1 2009 1 1 Australian Grand Prix 2009-03-29 06:00:00 http://en.wikipedia.org/wiki/2009_Australian_Grand_Prix \N \N \N \N \N \N \N \N \N \N 2 2009 2 2 Malaysian Grand Prix 2009-04-05 09:00:00 http://en.wikipedia.org/wiki/2009_Malaysian_Grand_Prix \N \N \N \N \N \N \N \N \N \N 3 2009 3 17 Chinese Grand Prix 2009-04-19 07:00:00 http://en.wikipedia.org/wiki/2009_Chinese_Grand_Prix \N \N \N \N \N \N \N \N \N \N

resultId raceId driverId constructorId number grid position positionText positionOrder points laps time milliseconds fastestLap rank fastestLapTime fastestLapSpeed statusId 1 18 1 1 22 1 1 1 1 10 58 1:34:50.616 5690616 39 2 1:27.452 218.300 1 2 18 2 2 3 5 2 2 2 8 58 +5.478 5696094 41 3 1:27.739 217.586 1 3 18 3 3 7 7 3 3 3 6 58 +8.163 5698779 41 5 1:28.090 216.719 1

raceId driverId stop lap time duration milliseconds 841 153 1 1 17:05:23 26.898 26898 841 30 1 1 17:05:52 25.021 25021 841 17 1 11 17:20:48 23.426 23426

statusId status 1 Finished 2 Disqualified 3 Accident

qualifyId raceId driverId constructorId number position q1 q2 q3 1 18 1 1 22 1 1:26.572 1:25.187 1:26.714 2 18 9 2 4 2 1:26.103 1:25.315 1:26.869 3 18 5 1 23 3 1:25.664 1:25.452 1:27.079

In [0]:
#Question 1: What was the average time each driver spent at the pit stop for each race?

# Calculate the average pit stop time per driver per race
avg_pit_times = df_pit_stops.groupBy("raceId", "driverId") \
                           .agg(avg("milliseconds").alias("avg_pit_time_ms")) \
                           .withColumn("avg_pit_time_seconds", col("avg_pit_time_ms") / 1000)

# Join with driver names for better readability
pit_stops_with_names = avg_pit_times.join(
    df_drivers.select("driverId", "forename", "surname"),
    on="driverId"
).withColumn("driver_name", concat(col("forename"), lit(" "), col("surname")))

# Join with race names
final_result = pit_stops_with_names.join(
    df_races.select("raceId", "name", "year"),
    on="raceId"
)

# Select and order the columns for display
q1_result = final_result.select(
    "year", "name", "driver_name", "avg_pit_time_seconds"
).orderBy("year", "name", "avg_pit_time_seconds")

# Display the results
display(q1_result)


year name driver_name avg_pit_time_seconds 2011 Abu Dhabi Grand Prix Pastor Maldonado 16.549 2011 Abu Dhabi Grand Prix Bruno Senna 18.057 2011 Abu Dhabi Grand Prix Lewis Hamilton 19.3945 2011 Abu Dhabi Grand Prix Nico Rosberg 19.846 2011 Abu Dhabi Grand Prix Michael Schumacher 20.149 2011 Abu Dhabi Grand Prix Paul di Resta 20.216 2011 Abu Dhabi Grand Prix Felipe Massa 20.253 2011 Abu Dhabi Grand Prix Vitaly Petrov 20.353 2011 Abu Dhabi Grand Prix Adrian Sutil 20.485 2011 Abu Dhabi Grand Prix Jenson Button 20.6045 2011 Abu Dhabi Grand Prix Fernando Alonso 20.7625 2011 Abu Dhabi Grand Prix Jarno Trulli 20.8075 2011 Abu Dhabi Grand Prix Heikki Kovalainen 20.899 2011 Abu Dhabi Grand Prix Timo Glock 21.1765 2011 Abu Dhabi Grand Prix Vitantonio Liuzzi 21.247 2011 Abu Dhabi Grand Prix Kamui Kobayashi 21.4705 2011 Abu Dhabi Grand Prix Mark Webber 21.569 2011 Abu Dhabi Grand Prix Sergio Pérez 22.3165 2011 Abu Dhabi Grand Prix Rubens Barrichello 22.3765 2011 Abu Dhabi Grand Prix Daniel Ricciardo 22.4425 2011 Abu Dhabi Grand Prix Jaime Alguersuari 32.4685 2011 Australian Grand Prix Jenson Button 20.950333333333333 2011 Australian Grand Prix Lewis Hamilton 23.213 2011 Australian Grand Prix Sebastian Vettel 23.3195 2011 Australian Grand Prix Sergio Pérez 23.438 2011 Australian Grand Prix Nico Rosberg 23.716 2011 Australian Grand Prix Timo Glock 23.792 2011 Australian Grand Prix Nick Heidfeld 24.046 2011 Australian Grand Prix Fernando Alonso 24.055 2011 Australian Grand Prix Mark Webber 24.058666666666667 2011 Australian Grand Prix Kamui Kobayashi 24.128 2011 Australian Grand Prix Felipe Massa 24.145666666666667 2011 Australian Grand Prix Sébastien Buemi 24.221 2011 Australian Grand Prix Michael Schumacher 24.5045 2011 Australian Grand Prix Paul di Resta 24.5975 2011 Australian Grand Prix Heikki Kovalainen 24.865 2011 Australian Grand Prix Jarno Trulli 24.8735 2011 Australian Grand Prix Adrian Sutil 24.9245 2011 Australian Grand Prix Vitaly Petrov 25.109 2011 Australian Grand Prix Jérôme d'Ambrosio 25.8525 2011 Australian Grand Prix Jaime Alguersuari 25.903 2011 Australian Grand Prix Rubens Barrichello 26.175 2011 Belgian Grand Prix Michael Schumacher 20.566 2011 Belgian Grand Prix Mark Webber 20.981 2011 Belgian Grand Prix Sebastian Vettel 21.031666666666666 2011 Belgian Grand Prix Fernando Alonso 21.1185 2011 Belgian Grand Prix Paul di Resta 21.342 2011 Belgian Grand Prix Sergio Pérez 21.354666666666667 2011 Belgian Grand Prix Vitaly Petrov 21.687 2011 Belgian Grand Prix Jarno Trulli 21.8215 2011 Belgian Grand Prix Bruno Senna 21.839666666666666 2011 Belgian Grand Prix Pastor Maldonado 21.862 2011 Belgian Grand Prix Felipe Massa 21.869333333333334 2011 Belgian Grand Prix Adrian Sutil 21.878 2011 Belgian Grand Prix Lewis Hamilton 21.895 2011 Belgian Grand Prix Nico Rosberg 22.1305 2011 Belgian Grand Prix Jérôme d'Ambrosio 22.5265 2011 Belgian Grand Prix Kamui Kobayashi 22.715 2011 Belgian Grand Prix Jenson Button 23.147333333333332 2011 Belgian Grand Prix Timo Glock 23.73275 2011 Belgian Grand Prix Daniel Ricciardo 23.78 2011 Belgian Grand Prix Heikki Kovalainen 24.284666666666666 2011 Belgian Grand Prix Vitantonio Liuzzi 26.3625 2011 Belgian Grand Prix Rubens Barrichello 30.349666666666668 2011 Brazilian Grand Prix Bruno Senna 20.3365 2011 Brazilian Grand Prix Nico Rosberg 20.7155 2011 Brazilian Grand Prix Lewis Hamilton 20.72533333333333 2011 Brazilian Grand Prix Fernando Alonso 20.729666666666667 2011 Brazilian Grand Prix Mark Webber 20.842 2011 Brazilian Grand Prix Adrian Sutil 21.045 2011 Brazilian Grand Prix Sebastian Vettel 21.22433333333333 2011 Brazilian Grand Prix Paul di Resta 21.256 2011 Brazilian Grand Prix Felipe Massa 21.3745 2011 Brazilian Grand Prix Jenson Button 21.542 2011 Brazilian Grand Prix Pastor Maldonado 21.561 2011 Brazilian Grand Prix Sergio Pérez 21.779 2011 Brazilian Grand Prix Rubens Barrichello 21.921666666666667 2011 Brazilian Grand Prix Vitaly Petrov 22.017333333333333 2011 Brazilian Grand Prix Jarno Trulli

In [0]:
#Rank the average time spent at the pit stop in order of who won each race

# Question 2: Rank the average time spent at the pit stop in order of who won each race

from pyspark.sql.functions import col, avg, concat, lit, rank
from pyspark.sql.window import Window

# Identify race winners (position = 1)
race_winners = df_results.filter(col("position") == 1) \
                        .select("raceId", "driverId") \
                        .withColumnRenamed("driverId", "winner_id")

# Calculate average pit stop time for each driver in each race
avg_pit_times = df_pit_stops.groupBy("raceId", "driverId") \
                           .agg(avg("milliseconds").alias("avg_pit_time_ms")) \
                           .withColumn("avg_pit_time_seconds", col("avg_pit_time_ms") / 1000)

# Join with race winners data
pit_times_with_winners = avg_pit_times.join(race_winners, on="raceId")

# Join with driver information for names
pit_times_with_names = pit_times_with_winners.join(
    df_drivers.select("driverId", "forename", "surname"),
    on="driverId"
).withColumn("driver_name", concat(col("forename"), lit(" "), col("surname")))

# Create a window function to rank pit stop times within each race
window_spec = Window.partitionBy("raceId").orderBy("avg_pit_time_ms")
ranked_pit_times = pit_times_with_names.withColumn("pit_time_rank", rank().over(window_spec))

# Mark the race winner
ranked_pit_times = ranked_pit_times.withColumn(
    "is_winner", 
    when(col("driverId") == col("winner_id"), lit("Race Winner")).otherwise(lit(""))
)

# Join with race information
final_result = ranked_pit_times.join(
    df_races.select("raceId", "name", "year"),
    on="raceId"
)

# Select and order columns for display
q2_result = final_result.select(
    "year", 
    "name", 
    "driver_name", 
    "avg_pit_time_seconds", 
    "pit_time_rank", 
    "is_winner"
).orderBy("year", "name", "pit_time_rank")

# Display the results
display(q2_result)

# Add a note about drivers who didn't finish or make pit stops
print("Note: Drivers who didn't finish the race or didn't make pit stops are not included in this analysis.")

year name driver_name avg_pit_time_seconds pit_time_rank is_winner 2011 Abu Dhabi Grand Prix Pastor Maldonado 16.549 1 2011 Abu Dhabi Grand Prix Bruno Senna 18.057 2 2011 Abu Dhabi Grand Prix Lewis Hamilton 19.3945 3 Race Winner 2011 Abu Dhabi Grand Prix Nico Rosberg 19.846 4 2011 Abu Dhabi Grand Prix Michael Schumacher 20.149 5 2011 Abu Dhabi Grand Prix Paul di Resta 20.216 6 2011 Abu Dhabi Grand Prix Felipe Massa 20.253 7 2011 Abu Dhabi Grand Prix Vitaly Petrov 20.353 8 2011 Abu Dhabi Grand Prix Adrian Sutil 20.485 9 2011 Abu Dhabi Grand Prix Jenson Button 20.6045 10 2011 Abu Dhabi Grand Prix Fernando Alonso 20.7625 11 2011 Abu Dhabi Grand Prix Jarno Trulli 20.8075 12 2011 Abu Dhabi Grand Prix Heikki Kovalainen 20.899 13 2011 Abu Dhabi Grand Prix Timo Glock 21.1765 14 2011 Abu Dhabi Grand Prix Vitantonio Liuzzi 21.247 15 2011 Abu Dhabi Grand Prix Kamui Kobayashi 21.4705 16 2011 Abu Dhabi Grand Prix Mark Webber 21.569 17 2011 Abu Dhabi Grand Prix Sergio Pérez 22.3165 18 2011 Abu Dhabi Grand Prix Rubens Barrichello 22.3765 19 2011 Abu Dhabi Grand Prix Daniel Ricciardo 22.4425 20 2011 Abu Dhabi Grand Prix Jaime Alguersuari 32.4685 21 2011 Australian Grand Prix Jenson Button 20.950333333333333 1 2011 Australian Grand Prix Lewis Hamilton 23.213 2 2011 Australian Grand Prix Sebastian Vettel 23.3195 3 Race Winner 2011 Australian Grand Prix Sergio Pérez 23.438 4 2011 Australian Grand Prix Nico Rosberg 23.716 5 2011 Australian Grand Prix Timo Glock 23.792 6 2011 Australian Grand Prix Nick Heidfeld 24.046 7 2011 Australian Grand Prix Fernando Alonso 24.055 8 2011 Australian Grand Prix Mark Webber 24.058666666666667 9 2011 Australian Grand Prix Kamui Kobayashi 24.128 10 2011 Australian Grand Prix Felipe Massa 24.145666666666667 11 2011 Australian Grand Prix Sébastien Buemi 24.221 12 2011 Australian Grand Prix Michael Schumacher 24.5045 13 2011 Australian Grand Prix Paul di Resta 24.5975 14 2011 Australian Grand Prix Heikki Kovalainen 24.865 15 2011 Australian Grand Prix Jarno Trulli 24.8735 16 2011 Australian Grand Prix Adrian Sutil 24.9245 17 2011 Australian Grand Prix Vitaly Petrov 25.109 18 2011 Australian Grand Prix Jérôme d'Ambrosio 25.8525 19 2011 Australian Grand Prix Jaime Alguersuari 25.903 20 2011 Australian Grand Prix Rubens Barrichello 26.175 21 2011 Belgian Grand Prix Michael Schumacher 20.566 1 2011 Belgian Grand Prix Mark Webber 20.981 2 2011 Belgian Grand Prix Sebastian Vettel 21.031666666666666 3 Race Winner 2011 Belgian Grand Prix Fernando Alonso 21.1185 4 2011 Belgian Grand Prix Paul di Resta 21.342 5 2011 Belgian Grand Prix Sergio Pérez 21.354666666666667 6 2011 Belgian Grand Prix Vitaly Petrov 21.687 7 2011 Belgian Grand Prix Jarno Trulli 21.8215 8 2011 Belgian Grand Prix Bruno Senna 21.839666666666666 9 2011 Belgian Grand Prix Pastor Maldonado 21.862 10 2011 Belgian Grand Prix Felipe Massa 21.869333333333334 11 2011 Belgian Grand Prix Adrian Sutil 21.878 12 2011 Belgian Grand Prix Lewis Hamilton 21.895 13 2011 Belgian Grand Prix Nico Rosberg 22.1305 14 2011 Belgian Grand Prix Jérôme d'Ambrosio 22.5265 15 2011 Belgian Grand Prix Kamui Kobayashi 22.715 16 2011 Belgian Grand Prix Jenson Button 23.147333333333332 17 2011 Belgian Grand Prix Timo Glock 23.73275 18 2011 Belgian Grand Prix Daniel Ricciardo 23.78 19 2011 Belgian Grand Prix Heikki Kovalainen 24.284666666666666 20 2011 Belgian Grand Prix Vitantonio Liuzzi 26.3625 21 2011 Belgian Grand Prix Rubens Barrichello 30.349666666666668 22 2011 Brazilian Grand Prix Bruno Senna 20.3365 1 2011 Brazilian Grand Prix Nico Rosberg 20.7155 2 2011 Brazilian Grand Prix Lewis Hamilton 20.72533333333333 3 2011 Brazilian Grand Prix Fernando Alonso 20.729666666666667 4 2011 Brazilian Grand Prix Mark Webber 20.842 5 Race Winner 2011 Brazilian Grand Prix Adrian Sutil 21.045 6 2011 Brazilian Grand Prix Sebastian Vettel 21.22433333333333 7 2011 Brazilian Grand Prix Paul di Resta 21.256 8 2011 Brazilian Grand Prix Felipe Massa 21.3745 9 2011 Brazilian Grand Prix Jenson Button 21.542 10

Note: Drivers who didn't finish the race or didn't make pit stops are not included in this analysis.


In [0]:
# Question 3: Insert the missing code (e.g: ALO for Alonso) for drivers based on the 'drivers' dataset

# Question 3: Insert the missing code for drivers based on the 'drivers' dataset

from pyspark.sql.functions import col, upper, substring, when, lit

# Check for drivers with missing codes 
# Let's try a different approach to identify missing codes
missing_codes = df_drivers.filter(
    (col("code").isNull()) | 
    (col("code") == "") | 
    (col("code") == "\\N") |  # This might be how NULL is represented in your data
    (col("code") == "N")
)

# Display drivers with missing codes
print("Drivers with missing codes:")
display(missing_codes)

# Count how many drivers are missing codes
missing_code_count = missing_codes.count()
print(f"Number of drivers missing codes: {missing_code_count}")

# Generate three-letter codes for ALL drivers
df_drivers_with_codes = df_drivers.withColumn(
    "generated_code",
    when((col("code").isNull()) | (col("code") == "") | (col("code") == "\\N") | (col("code") == "N"),
         upper(substring(col("surname"), 1, 3))
    ).otherwise(col("code"))
)

# Display all drivers with their original and generated codes
display(df_drivers_with_codes.select(
    "driverId", 
    "forename", 
    "surname", 
    "code", 
    "generated_code"
).orderBy("driverId"))

# Now let's specifically check which drivers got NEW codes
drivers_with_new_codes = df_drivers_with_codes.filter(
    col("code") != col("generated_code")
)

print("Drivers who received newly generated codes:")
display(drivers_with_new_codes.select(
    "driverId", 
    "forename", 
    "surname", 
    "code", 
    "generated_code"
).orderBy("driverId"))

Drivers with missing codes:


driverId driverRef number code forename surname dob nationality url 43 matta \N \N Cristiano da Matta 1973-09-19 Brazilian http://en.wikipedia.org/wiki/Cristiano_da_Matta 44 panis \N \N Olivier Panis 1966-09-02 French http://en.wikipedia.org/wiki/Olivier_Panis 45 pantano \N \N Giorgio Pantano 1979-02-04 Italian http://en.wikipedia.org/wiki/Giorgio_Pantano 46 bruni \N \N Gianmaria Bruni 1981-05-30 Italian http://en.wikipedia.org/wiki/Gianmaria_Bruni 47 baumgartner \N \N Zsolt Baumgartner 1981-01-01 Hungarian http://en.wikipedia.org/wiki/Zsolt_Baumgartner 48 gene \N \N Marc Gené 1974-03-29 Spanish http://en.wikipedia.org/wiki/Marc_Gen%C3%A9 49 frentzen \N \N Heinz-Harald Frentzen 1967-05-18 German http://en.wikipedia.org/wiki/Heinz-Harald_Frentzen 50 verstappen \N \N Jos Verstappen 1972-03-04 Dutch http://en.wikipedia.org/wiki/Jos_Verstappen 51 wilson \N \N Justin Wilson 1978-07-31 British http://en.wikipedia.org/wiki/Justin_Wilson_(racing_driver) 52 firman \N \N Ralph Firman 1975-05-20 Irish http://en.wikipedia.org/wiki/Ralph_Firman 53 kiesa \N \N Nicolas Kiesa 1978-03-03 Danish http://en.wikipedia.org/wiki/Nicolas_Kiesa 54 burti \N \N Luciano Burti 1975-03-05 Brazilian http://en.wikipedia.org/wiki/Luciano_Burti 55 alesi \N \N Jean Alesi 1964-06-11 French http://en.wikipedia.org/wiki/Jean_Alesi 56 irvine \N \N Eddie Irvine 1965-11-10 British http://en.wikipedia.org/wiki/Eddie_Irvine 57 hakkinen \N \N Mika Häkkinen 1968-09-28 Finnish http://en.wikipedia.org/wiki/Mika_H%C3%A4kkinen 58 marques \N \N Tarso Marques 1976-01-19 Brazilian http://en.wikipedia.org/wiki/Tarso_Marques 59 bernoldi \N \N Enrique Bernoldi 1978-10-19 Brazilian http://en.wikipedia.org/wiki/Enrique_Bernoldi 60 mazzacane \N \N Gastón Mazzacane 1975-05-08 Argentine http://en.wikipedia.org/wiki/Gast%C3%B3n_Mazzacane 61 enge \N \N Tomáš Enge 1976-09-11 Czech http://en.wikipedia.org/wiki/Tom%C3%A1%C5%A1_Enge 62 yoong \N \N Alex Yoong 1976-07-20 Malaysian http://en.wikipedia.org/wiki/Alex_Yoong 63 salo \N \N Mika Salo 1966-11-30 Finnish http://en.wikipedia.org/wiki/Mika_Salo 64 diniz \N \N Pedro Diniz 1970-05-22 Brazilian http://en.wikipedia.org/wiki/Pedro_Diniz 65 herbert \N \N Johnny Herbert 1964-06-25 British http://en.wikipedia.org/wiki/Johnny_Herbert 66 mcnish \N \N Allan McNish 1969-12-29 British http://en.wikipedia.org/wiki/Allan_McNish 68 takagi \N \N Toranosuke Takagi 1974-02-12 Japanese http://en.wikipedia.org/wiki/Toranosuke_Takagi 70 zanardi \N \N Alessandro Zanardi 1966-10-23 Italian http://en.wikipedia.org/wiki/Alex_Zanardi 71 damon_hill \N \N Damon Hill 1960-09-17 British http://en.wikipedia.org/wiki/Damon_Hill 72 sarrazin \N \N Stéphane Sarrazin 1975-11-02 French http://en.wikipedia.org/wiki/St%C3%A9phane_Sarrazin 73 rosset \N \N Ricardo Rosset 1968-07-27 Brazilian http://en.wikipedia.org/wiki/Ricardo_Rosset 74 tuero \N \N Esteban Tuero 1978-04-22 Argentine http://en.wikipedia.org/wiki/Esteban_Tuero 75 nakano \N \N Shinji Nakano 1971-04-01 Japanese http://en.wikipedia.org/wiki/Shinji_Nakano 77 berger \N \N Gerhard Berger 1959-08-27 Austrian http://en.wikipedia.org/wiki/Gerhard_Berger 78 larini \N \N Nicola Larini 1964-03-19 Italian http://en.wikipedia.org/wiki/Nicola_Larini 79 katayama \N \N Ukyo Katayama 1963-05-29 Japanese http://en.wikipedia.org/wiki/Ukyo_Katayama 80 sospiri \N \N Vincenzo Sospiri 1966-10-07 Italian http://en.wikipedia.org/wiki/Vincenzo_Sospiri 81 morbidelli \N \N Gianni Morbidelli 1968-01-13 Italian http://en.wikipedia.org/wiki/Gianni_Morbidelli 82 fontana \N \N Norberto Fontana 1975-01-20 Argentine http://en.wikipedia.org/wiki/Norberto_Fontana 83 lamy \N \N Pedro Lamy 1972-03-20 Portuguese http://en.wikipedia.org/wiki/Pedro_Lamy 84 brundle \N \N Martin Brundle 1959-06-01 British http://en.wikipedia.org/wiki/Martin_Brundle 85 montermini \N \N Andrea Montermini 1964-05-30 Italian http://en.wikipedia.org/wiki/Andrea_Montermini 86 lavaggi \N \N Giovanni Lavaggi 1958-02-18 Italian http://en.wikipedia.org/wiki/Giovanni_Lavaggi 87 blunde

Number of drivers missing codes: 757


driverId forename surname code generated_code 1 Lewis Hamilton HAM HAM 10 Timo Glock GLO GLO 100 Érik Comas \N COM 101 David Brabham \N BRA 102 Ayrton Senna \N SEN 103 Éric Bernard \N BER 104 Christian Fittipaldi \N FIT 105 Michele Alboreto \N ALB 106 Olivier Beretta \N BER 107 Roland Ratzenberger \N RAT 108 Paul Belmondo \N BEL 109 Jyrki Järvilehto \N JÄR 11 Takuma Sato SAT SAT 110 Andrea de Cesaris \N DE 111 Jean-Marc Gounon \N GOU 112 Philippe Alliot \N ALL 113 Philippe Adams \N ADA 114 Yannick Dalmas \N DAL 115 Hideki Noda \N NOD 116 Franck Lagorce \N LAG 117 Alain Prost \N PRO 118 Derek Warwick \N WAR 119 Riccardo Patrese \N PAT 12 Nelson Piquet Jr. PIQ PIQ 120 Fabrizio Barbazza \N BAR 121 Michael Andretti \N AND 122 Ivan Capelli \N CAP 123 Thierry Boutsen \N BOU 124 Marco Apicella \N API 125 Emanuele Naspetti \N NAS 126 Toshio Suzuki \N SUZ 127 Maurício Gugelmin \N GUG 128 Eric van de Poele \N VAN 129 Olivier Grouillard \N GRO 13 Felipe Massa MAS MAS 130 Andrea Chiesa \N CHI 131 Stefano Modena \N MOD 132 Giovanna Amati \N AMA 133 Alex Caffi \N CAF 134 Enrico Bertaggia \N BER 135 Perry McCarthy \N MCC 136 Jan Lammers \N LAM 137 Nelson Piquet \N PIQ 138 Satoru Nakajima \N NAK 139 Emanuele Pirro \N PIR 14 David Coulthard COU COU 140 Stefan Johansson \N JOH 141 Julian Bailey \N BAI 142 Pedro Chaves \N CHA 143 Michael Bartels \N BAR 144 Naoki Hattori \N HAT 145 Alessandro Nannini \N NAN 146 Bernd Schneider \N SCH 147 Paolo Barilla \N BAR 148 Gregor Foitek \N FOI 149 Claudio Langes \N LAN 15 Jarno Trulli TRU TRU 150 Gary Brabham \N BRA 151 Martin Donnelly \N DON 152 Bruno Giacomelli \N GIA 153 Jaime Alguersuari ALG ALG 154 Romain Grosjean GRO GRO 155 Kamui Kobayashi KOB KOB 156 Jonathan Palmer \N PAL 157 Christian Danner \N DAN 158 Eddie Cheever \N CHE 159 Luis Pérez-Sala \N PÉR 16 Adrian Sutil SUT SUT 160 Piercarlo Ghinzani \N GHI 161 Volker Weidler \N WEI 162 Pierre-Henri Raphanel \N RAP 163 René Arnoux \N ARN 164 Joachim Winkelhock \N WIN 165 Oscar Larrauri \N LAR 166 Philippe Streiff \N STR 167 Adrián Campos \N CAM 168 Jean-Louis Schlesser \N SCH 169 Pascal Fabre \N FAB 17 Mark Webber WEB WEB 170 Teo Fabi \N FAB 171 Franco Forini \N FOR 172 Jacques Laffite \N LAF 173 Elio de Angelis \N DE 174 Johnny Dumfries \N DUM 175 Patrick Tambay \N TAM 176 Marc Surer \N SUR 177 Keke Rosberg \N ROS 178 Alan Jones \N JON 179 Huub Rothengatter \N ROT 18 Jenson Button BUT BUT 180 Allen Berg \N BER 181 Manfred Winkelhock \N WIN 182 Niki Lauda \N LAU 183 François Hesnault \N HES 184 Mauro Baldi \N BAL 185 Stefan Bellof \N BEL 186 Kenny Acheson \N ACH 187 John Watson \N WAT 188 Johnny Cecotto \N CEC 189 Jo Gartner \N GAR 19 Anthony Davidson DAV DAV 190 Corrado Fabi \N FAB 191 Mike Thackwell \N THA 192 Chico Serra \N SER 193 Danny Sullivan \N SUL 194 Eliseo Salazar \N SAL 195 Roberto Guerrero \N GUE 196 Raul Boesel \N BOE 197 Jean-Pierre Jarier \N JAR 198 Jacques Villeneuve Sr. \N VIL 199 Carlos Reutemann \N REU 2 Nick Heidfeld HEI HEI 20 Sebastian Vettel VET VET 200 Jochen Mass \N MAS 201 Slim Borgudd \N BOR 202 Didier Pironi \N PIR 203 Gilles Villeneuve \N VIL 204 Riccardo Paletti \N PAL 205 Brian Henton \N HEN 206 Derek Daly \N DAL 207 Mario Andretti \N AND 208 Emilio de Villota \N DE 209 Geoff Lees \N LEE 21 Giancarlo Fisichella FIS FIS 210 Tommy Byrne \N BYR 211 Rupert Keegan \N KEE 212 Hector Rebaque \N REB 213 Beppe Gabbiani \N GAB 214 Kevin Cogan \N COG 215 Miguel Ángel Guerra \N GUE 216 Siegfried Stohr \N STO 217 Ricardo Zunino \N ZUN 218 Ricardo Londoño \N LON 219 Jean-Pierre Jabouille \N JAB 22 Rubens Barrichello BAR BAR 220 Giorgio Francia \N FRA 221 Patrick Depailler \N DEP 222 Jody Scheckter \N SCH 223 Clay Regazzoni \N REG 224 Emerson Fittipaldi \N FIT 225 Dave Kennedy \N KEN 226 Stephen South \N SOU 227 Tiff Needell \N NEE 228 Desiré Wilson \N WIL 229 Harald Ertl \N ERT 23 Ralf Schumacher SCH SCH 230 Vittorio Brambilla \N BRA 231 James Hunt \N HUN 232 Arturo Merzario \N MER 233 Hans-Joachim Stuck \N STU 234 Gianfranco Brancate

Drivers who received newly generated codes:


driverId forename surname code generated_code 100 Érik Comas \N COM 101 David Brabham \N BRA 102 Ayrton Senna \N SEN 103 Éric Bernard \N BER 104 Christian Fittipaldi \N FIT 105 Michele Alboreto \N ALB 106 Olivier Beretta \N BER 107 Roland Ratzenberger \N RAT 108 Paul Belmondo \N BEL 109 Jyrki Järvilehto \N JÄR 110 Andrea de Cesaris \N DE 111 Jean-Marc Gounon \N GOU 112 Philippe Alliot \N ALL 113 Philippe Adams \N ADA 114 Yannick Dalmas \N DAL 115 Hideki Noda \N NOD 116 Franck Lagorce \N LAG 117 Alain Prost \N PRO 118 Derek Warwick \N WAR 119 Riccardo Patrese \N PAT 120 Fabrizio Barbazza \N BAR 121 Michael Andretti \N AND 122 Ivan Capelli \N CAP 123 Thierry Boutsen \N BOU 124 Marco Apicella \N API 125 Emanuele Naspetti \N NAS 126 Toshio Suzuki \N SUZ 127 Maurício Gugelmin \N GUG 128 Eric van de Poele \N VAN 129 Olivier Grouillard \N GRO 130 Andrea Chiesa \N CHI 131 Stefano Modena \N MOD 132 Giovanna Amati \N AMA 133 Alex Caffi \N CAF 134 Enrico Bertaggia \N BER 135 Perry McCarthy \N MCC 136 Jan Lammers \N LAM 137 Nelson Piquet \N PIQ 138 Satoru Nakajima \N NAK 139 Emanuele Pirro \N PIR 140 Stefan Johansson \N JOH 141 Julian Bailey \N BAI 142 Pedro Chaves \N CHA 143 Michael Bartels \N BAR 144 Naoki Hattori \N HAT 145 Alessandro Nannini \N NAN 146 Bernd Schneider \N SCH 147 Paolo Barilla \N BAR 148 Gregor Foitek \N FOI 149 Claudio Langes \N LAN 150 Gary Brabham \N BRA 151 Martin Donnelly \N DON 152 Bruno Giacomelli \N GIA 156 Jonathan Palmer \N PAL 157 Christian Danner \N DAN 158 Eddie Cheever \N CHE 159 Luis Pérez-Sala \N PÉR 160 Piercarlo Ghinzani \N GHI 161 Volker Weidler \N WEI 162 Pierre-Henri Raphanel \N RAP 163 René Arnoux \N ARN 164 Joachim Winkelhock \N WIN 165 Oscar Larrauri \N LAR 166 Philippe Streiff \N STR 167 Adrián Campos \N CAM 168 Jean-Louis Schlesser \N SCH 169 Pascal Fabre \N FAB 170 Teo Fabi \N FAB 171 Franco Forini \N FOR 172 Jacques Laffite \N LAF 173 Elio de Angelis \N DE 174 Johnny Dumfries \N DUM 175 Patrick Tambay \N TAM 176 Marc Surer \N SUR 177 Keke Rosberg \N ROS 178 Alan Jones \N JON 179 Huub Rothengatter \N ROT 180 Allen Berg \N BER 181 Manfred Winkelhock \N WIN 182 Niki Lauda \N LAU 183 François Hesnault \N HES 184 Mauro Baldi \N BAL 185 Stefan Bellof \N BEL 186 Kenny Acheson \N ACH 187 John Watson \N WAT 188 Johnny Cecotto \N CEC 189 Jo Gartner \N GAR 190 Corrado Fabi \N FAB 191 Mike Thackwell \N THA 192 Chico Serra \N SER 193 Danny Sullivan \N SUL 194 Eliseo Salazar \N SAL 195 Roberto Guerrero \N GUE 196 Raul Boesel \N BOE 197 Jean-Pierre Jarier \N JAR 198 Jacques Villeneuve Sr. \N VIL 199 Carlos Reutemann \N REU 200 Jochen Mass \N MAS 201 Slim Borgudd \N BOR 202 Didier Pironi \N PIR 203 Gilles Villeneuve \N VIL 204 Riccardo Paletti \N PAL 205 Brian Henton \N HEN 206 Derek Daly \N DAL 207 Mario Andretti \N AND 208 Emilio de Villota \N DE 209 Geoff Lees \N LEE 210 Tommy Byrne \N BYR 211 Rupert Keegan \N KEE 212 Hector Rebaque \N REB 213 Beppe Gabbiani \N GAB 214 Kevin Cogan \N COG 215 Miguel Ángel Guerra \N GUE 216 Siegfried Stohr \N STO 217 Ricardo Zunino \N ZUN 218 Ricardo Londoño \N LON 219 Jean-Pierre Jabouille \N JAB 220 Giorgio Francia \N FRA 221 Patrick Depailler \N DEP 222 Jody Scheckter \N SCH 223 Clay Regazzoni \N REG 224 Emerson Fittipaldi \N FIT 225 Dave Kennedy \N KEN 226 Stephen South \N SOU 227 Tiff Needell \N NEE 228 Desiré Wilson \N WIL 229 Harald Ertl \N ERT 230 Vittorio Brambilla \N BRA 231 James Hunt \N HUN 232 Arturo Merzario \N MER 233 Hans-Joachim Stuck \N STU 234 Gianfranco Brancatelli \N BRA 235 Jacky Ickx \N ICK 236 Patrick Gaillard \N GAI 237 Alex Ribeiro \N RIB 238 Ronnie Peterson \N PET 239 Brett Lunger \N LUN 240 Danny Ongais \N ONG 241 Lamberto Leoni \N LEO 242 Divina Galica \N GAL 243 Rolf Stommelen \N STO 244 Alberto Colombo \N COL 245 Tony Trimmer \N TRI 246 Hans Binder \N BIN 247 Michael Bleekemolen \N BLE 248 Carlo Franchi \N FRA 249 Bobby Rahal \N RAH 250 Carlos Pace \N PAC 251 Ian Scheckter \N SCH 252 Tom Pryce \N PRY 253 Ingo Hoffmann \N HOF 254 Renzo Zorzi \

In [0]:
# Question 4: Who is the youngest and oldest driver for each race? Create a new column called “Age”

from pyspark.sql.functions import col, datediff, year, lit, concat, rank
from pyspark.sql.window import Window
from pyspark.sql.types import IntegerType

# First, get all driver-race combinations from results
race_participants = df_results.select("raceId", "driverId").distinct()

# Get race dates from the races table
race_dates = df_races.select("raceId", "date", "name", "year")

# Join races and drivers to calculate age at race time
driver_ages = race_participants.join(race_dates, on="raceId") \
                              .join(df_drivers.select("driverId", "dob", "forename", "surname"), on="driverId") \
                              .withColumn("race_date", col("date").cast("date")) \
                              .withColumn("birth_date", col("dob").cast("date")) \
                              .withColumn("age_years", (datediff(col("race_date"), col("birth_date")) / 365.25).cast(IntegerType())) \
                              .withColumn("driver_name", concat(col("forename"), lit(" "), col("surname")))

# Define windows for finding youngest and oldest drivers per race
window_youngest = Window.partitionBy("raceId").orderBy("age_years")
window_oldest = Window.partitionBy("raceId").orderBy(col("age_years").desc())

# Find youngest driver for each race
youngest_drivers = driver_ages.withColumn("rank", rank().over(window_youngest)) \
                             .filter(col("rank") == 1) \
                             .select("raceId", "driver_name", "age_years") \
                             .withColumnRenamed("driver_name", "youngest_driver") \
                             .withColumnRenamed("age_years", "youngest_age")

# Find oldest driver for each race
oldest_drivers = driver_ages.withColumn("rank", rank().over(window_oldest)) \
                           .filter(col("rank") == 1) \
                           .select("raceId", "driver_name", "age_years") \
                           .withColumnRenamed("driver_name", "oldest_driver") \
                           .withColumnRenamed("age_years", "oldest_age")

# Combine youngest and oldest driver information
age_results = youngest_drivers.join(oldest_drivers, on="raceId") \
                             .join(race_dates, on="raceId") \
                             .select("year", "name", "youngest_driver", "youngest_age", "oldest_driver", "oldest_age")

# Display the results sorted by year and race name
display(age_results.orderBy("year", "name"))

# Also save the original driver_ages DataFrame which contains the "Age" column for all drivers
display(driver_ages.select("raceId", "name", "year", "driver_name", "age_years").orderBy("year", "name", "driver_name"))

# Add explanation of the age calculation approach
"""
Age Calculation Approach:
1. Created a new "age_years" column that calculates each driver's age at the time of the race
2. Age is calculated by finding the difference between race date and birth date in days
3. Divided this difference by 365.25 to convert to years (accounting for leap years)
4. For each race, identified both the youngest and oldest driver
5. This approach gives an accurate age count based on how many birthdays each driver had experienced by race day
"""

year name youngest_driver youngest_age oldest_driver oldest_age 1950 Belgian Grand Prix Geoff Crossley 29 Philippe Étancelin 53 1950 British Grand Prix Geoff Crossley 29 Philippe Étancelin 53 1950 French Grand Prix José Froilán González 27 Philippe Étancelin 53 1950 Indianapolis 500 Jimmy Davies 20 Mauri Rose 44 1950 Indianapolis 500 Troy Ruttman 20 Mauri Rose 44 1950 Italian Grand Prix Alberto Ascari 32 Philippe Étancelin 53 1950 Italian Grand Prix Maurice Trintignant 32 Philippe Étancelin 53 1950 Monaco Grand Prix José Froilán González 27 Philippe Étancelin 53 1950 Swiss Grand Prix Harry Schell 28 Philippe Étancelin 53 1951 Belgian Grand Prix Alberto Ascari 32 Philippe Étancelin 54 1951 Belgian Grand Prix André Pilette 32 Philippe Étancelin 54 1951 British Grand Prix José Froilán González 28 Louis Chiron 51 1951 French Grand Prix Onofre Marimón 27 Philippe Étancelin 54 1951 German Grand Prix Jacques Swaters 24 Philippe Étancelin 54 1951 Indianapolis 500 Jimmy Davies 21 Chet Miller 48 1951 Indianapolis 500 Troy Ruttman 21 Chet Miller 48 1951 Italian Grand Prix Jacques Swaters 24 Louis Chiron 52 1951 Spanish Grand Prix José Froilán González 29 Philippe Étancelin 54 1951 Swiss Grand Prix Stirling Moss 21 Philippe Étancelin 54 1952 Belgian Grand Prix Peter Collins 20 Arthur Legat 53 1952 British Grand Prix Peter Collins 20 Bill Aston 52 1952 Dutch Grand Prix Stirling Moss 22 Nino Farina 45 1952 Dutch Grand Prix Stirling Moss 22 Chico Landi 45 1952 French Grand Prix Peter Collins 20 Philippe Étancelin 55 1952 German Grand Prix Fritz Riess 30 Bill Aston 52 1952 German Grand Prix Fritz Riess 30 Adolf Brudes 52 1952 German Grand Prix Willi Heeks 30 Bill Aston 52 1952 German Grand Prix Willi Heeks 30 Adolf Brudes 52 1952 German Grand Prix Günther Bechem 30 Bill Aston 52 1952 German Grand Prix Günther Bechem 30 Adolf Brudes 52 1952 Indianapolis 500 Troy Ruttman 22 Chet Miller 49 1952 Indianapolis 500 Jimmy Reece 22 Chet Miller 49 1952 Italian Grand Prix Peter Collins 20 Bill Aston 52 1952 Italian Grand Prix Peter Collins 20 Piero Dusio 52 1952 Swiss Grand Prix Peter Collins 20 Hans von Stuck 51 1953 Argentine Grand Prix Mike Hawthorn 23 Felice Bonetto 49 1953 Argentine Grand Prix John Barber 23 Felice Bonetto 49 1953 Belgian Grand Prix Peter Collins 21 Arthur Legat 54 1953 British Grand Prix Peter Collins 21 Felice Bonetto 50 1953 Dutch Grand Prix Peter Collins 21 Felice Bonetto 49 1953 French Grand Prix Peter Collins 21 Louis Chiron 53 1953 German Grand Prix Stirling Moss 23 Hans von Stuck 52 1953 Indianapolis 500 Jimmy Davies 23 Bill Holland 45 1953 Italian Grand Prix Stirling Moss 23 Louis Chiron 54 1953 Swiss Grand Prix Mike Hawthorn 24 Felice Bonetto 50 1954 Argentine Grand Prix Mike Hawthorn 24 Louis Rosier 48 1954 Belgian Grand Prix Stirling Moss 24 Nino Farina 47 1954 British Grand Prix Peter Collins 22 Louis Rosier 48 1954 French Grand Prix Sergio Mantovani 25 Louis Rosier 48 1954 French Grand Prix Mike Hawthorn 25 Louis Rosier 48 1954 German Grand Prix Stirling Moss 24 Louis Rosier 48 1954 Indianapolis 500 Jimmy Davies 24 Travis Webb 43 1954 Indianapolis 500 Jimmy Davies 24 Jimmy Jackson 43 1954 Indianapolis 500 Troy Ruttman 24 Travis Webb 43 1954 Indianapolis 500 Troy Ruttman 24 Jimmy Jackson 43 1954 Indianapolis 500 Jimmy Reece 24 Travis Webb 43 1954 Indianapolis 500 Jimmy Reece 24 Jimmy Jackson 43 1954 Italian Grand Prix Peter Collins 22 Louis Rosier 48 1954 Spanish Grand Prix Peter Collins 22 Louis Rosier 48 1954 Swiss Grand Prix Stirling Moss 24 Juan Fangio 43 1954 Swiss Grand Prix Stirling Moss 24 Karl Kling 43 1955 Argentine Grand Prix Eugenio Castellotti 24 Nino Farina 48 1955 Belgian Grand Prix Cesare Perdisa 22 Louis Rosier 49 1955 British Grand Prix Peter Collins 23 Piero Taruffi 48 1955 Dutch Grand Prix Eugenio Castellotti 24 Louis Rosier 49 1955 Indianapolis 500 Jimmy Davies 25 Duane Carter 42 1955 Indianapolis 500 Jimmy Reece 25 Duane Carter 42 1955 Italian Grand Prix Peter Collins 23 Piero Taruffi 48 1955 Ital

raceId name year driver_name age_years 837 Belgian Grand Prix 1950 Alberto Ascari 31 837 Belgian Grand Prix 1950 Eugène Chaboud 43 837 Belgian Grand Prix 1950 Geoff Crossley 29 837 Belgian Grand Prix 1950 Johnny Claes 33 837 Belgian Grand Prix 1950 Juan Fangio 38 837 Belgian Grand Prix 1950 Louis Rosier 44 837 Belgian Grand Prix 1950 Luigi Fagioli 52 837 Belgian Grand Prix 1950 Luigi Villoresi 41 837 Belgian Grand Prix 1950 Nino Farina 43 837 Belgian Grand Prix 1950 Philippe Étancelin 53 837 Belgian Grand Prix 1950 Pierre Levegh 44 837 Belgian Grand Prix 1950 Raymond Sommer 43 837 Belgian Grand Prix 1950 Toni Branca 33 837 Belgian Grand Prix 1950 Yves Cabantous 45 833 British Grand Prix 1950 Bob Gerard 36 833 British Grand Prix 1950 Brian Shawe Taylor 35 833 British Grand Prix 1950 Cuth Harrison 43 833 British Grand Prix 1950 David Hampshire 32 833 British Grand Prix 1950 David Murray 40 833 British Grand Prix 1950 Eugène Martin 35 833 British Grand Prix 1950 Geoff Crossley 29 833 British Grand Prix 1950 Joe Fry 34 833 British Grand Prix 1950 Joe Kelly 37 833 British Grand Prix 1950 Johnny Claes 33 833 British Grand Prix 1950 Juan Fangio 38 833 British Grand Prix 1950 Leslie Johnson 38 833 British Grand Prix 1950 Louis Chiron 50 833 British Grand Prix 1950 Louis Rosier 44 833 British Grand Prix 1950 Luigi Fagioli 51 833 British Grand Prix 1950 Nino Farina 43 833 British Grand Prix 1950 Peter Walker 37 833 British Grand Prix 1950 Philippe Étancelin 53 833 British Grand Prix 1950 Prince Bira 35 833 British Grand Prix 1950 Reg Parnell 38 833 British Grand Prix 1950 Tony Rolt 31 833 British Grand Prix 1950 Toulo de Graffenried 35 833 British Grand Prix 1950 Yves Cabantous 45 838 French Grand Prix 1950 Charles Pozzi 40 838 French Grand Prix 1950 David Hampshire 32 838 French Grand Prix 1950 Eugène Chaboud 43 838 French Grand Prix 1950 Felice Bonetto 47 838 French Grand Prix 1950 Franco Rol 42 838 French Grand Prix 1950 Johnny Claes 33 838 French Grand Prix 1950 José Froilán González 27 838 French Grand Prix 1950 Juan Fangio 39 838 French Grand Prix 1950 Louis Chiron 50 838 French Grand Prix 1950 Louis Rosier 44 838 French Grand Prix 1950 Luigi Fagioli 52 838 French Grand Prix 1950 Nino Farina 43 838 French Grand Prix 1950 Peter Whitehead 35 838 French Grand Prix 1950 Philippe Étancelin 53 838 French Grand Prix 1950 Pierre Levegh 44 838 French Grand Prix 1950 Raymond Sommer 43 838 French Grand Prix 1950 Reg Parnell 39 838 French Grand Prix 1950 Robert Manzon 33 838 French Grand Prix 1950 Yves Cabantous 45 835 Indianapolis 500 1950 Bayliss Levrett 36 835 Indianapolis 500 1950 Bill Cantrell 42 835 Indianapolis 500 1950 Bill Holland 42 835 Indianapolis 500 1950 Bill Schindler 41 835 Indianapolis 500 1950 Cecil Green 30 835 Indianapolis 500 1950 Dick Rathmann 26 835 Indianapolis 500 1950 Duane Carter 37 835 Indianapolis 500 1950 Duke Dinsmore 37 835 Indianapolis 500 1950 Fred Agabashian 36 835 Indianapolis 500 1950 Gene Hartley 24 835 Indianapolis 500 1950 George Connor 43 835 Indianapolis 500 1950 Henry Banks 36 835 Indianapolis 500 1950 Jack McGrath 30 835 Indianapolis 500 1950 Jackie Holmes 29 835 Indianapolis 500 1950 Jerry Hoyt 21 835 Indianapolis 500 1950 Jim Rathmann 21 835 Indianapolis 500 1950 Jimmy Davies 20 835 Indianapolis 500 1950 Jimmy Jackson 39 835 Indianapolis 500 1950 Johnnie Parsons 31 835 Indianapolis 500 1950 Johnny McDowell 35 835 Indianapolis 500 1950 Joie Chitwood 38 835 Indianapolis 500 1950 Lee Wallard 39 835 Indianapolis 500 1950 Mack Hellings 34 835 Indianapolis 500 1950 Mauri Rose 44 835 Indianapolis 500 1950 Myron Fohr 37 835 Indianapolis 500 1950 Pat Flaherty 24 835 Indianapolis 500 1950 Paul Russo 36 835 Indianapolis 500 1950 Sam Hanks 35 835 Indianapolis 500 1950 Tony Bettenhausen 33 835 Indianapolis 500 1950 Travis Webb 39 835 Indianapolis 500 1950 Troy Ruttman 20 835 Indianapolis 500 1950 Walt Ader 36 835 Indianapolis 500 1950 Walt Brown 38 835 Indianapolis 500 1950 Walt Faulkner 30 839 Italian Grand P

'\nAge Calculation Approach:\n1. Created a new "age_years" column that calculates each driver\'s age at the time of the race\n2. Age is calculated by finding the difference between race date and birth date in days\n3. Divided this difference by 365.25 to convert to years (accounting for leap years)\n4. For each race, identified both the youngest and oldest driver\n5. This approach gives an accurate age count based on how many birthdays each driver had experienced by race day\n'

In [0]:
# Question 6 (my own) : Which nationality is most common for the drivers? 

# Question 6: Which nationality is the most common among F1 drivers?

from pyspark.sql.functions import count, desc

# Count the number of drivers by nationality
nationality_counts = df_drivers.groupBy("nationality") \
                              .agg(count("driverId").alias("driver_count"))

# Sort by count in descending order to see most common nationalities
sorted_nationalities = nationality_counts.orderBy(desc("driver_count"))

# Display the results
display(sorted_nationalities)

# Calculate percentage of total for each nationality
total_drivers = df_drivers.count()
nationality_percentages = nationality_counts.withColumn(
    "percentage", 
    (col("driver_count") / total_drivers * 100).cast("decimal(5,2)")
)

# Sort by percentage in descending order
sorted_percentages = nationality_percentages.orderBy(desc("percentage"))

# Display the results with percentages
display(sorted_percentages)

# Create a visualization showing the top 10 nationalities
top_10_nationalities = sorted_nationalities.limit(10)
display(top_10_nationalities)

# Add explanation
"""
Nationality Analysis:
1. Counted the number of drivers from each nationality
2. Calculated what percentage of total F1 drivers each nationality represents
3. Identified the most common nationality in Formula 1 history
4. This analysis helps understand which countries have contributed the most drivers to F1
"""

nationality driver_count British 165 American 158 Italian 99 French 73 German 50 Brazilian 32 Argentine 24 Swiss 23 South African 23 Belgian 23 Japanese 20 Australian 18 Dutch 18 Spanish 15 Austrian 15 Canadian 14 Swedish 10 Finnish 9 New Zealander 9 Mexican 6 Irish 5 Danish 5 Rhodesian 4 Portuguese 4 Russian 4 Uruguayan 4 Monegasque 4 East German 3 Colombian 3 Venezuelan 3 Thai 2 Indian 2 Chinese 1 Indonesian 1 Argentine-Italian 1 Chilean 1 Polish 1 Hungarian 1 American-Italian 1 Malaysian 1 Liechtensteiner 1 Czech 1

nationality driver_count percentage British 165 19.25 American 158 18.44 Italian 99 11.55 French 73 8.52 German 50 5.83 Brazilian 32 3.73 Argentine 24 2.80 Swiss 23 2.68 South African 23 2.68 Belgian 23 2.68 Japanese 20 2.33 Australian 18 2.10 Dutch 18 2.10 Spanish 15 1.75 Austrian 15 1.75 Canadian 14 1.63 Swedish 10 1.17 Finnish 9 1.05 New Zealander 9 1.05 Mexican 6 0.70 Irish 5 0.58 Danish 5 0.58 Rhodesian 4 0.47 Portuguese 4 0.47 Russian 4 0.47 Uruguayan 4 0.47 Monegasque 4 0.47 East German 3 0.35 Colombian 3 0.35 Venezuelan 3 0.35 Thai 2 0.23 Indian 2 0.23 Chinese 1 0.12 Indonesian 1 0.12 Argentine-Italian 1 0.12 Chilean 1 0.12 Polish 1 0.12 Hungarian 1 0.12 American-Italian 1 0.12 Malaysian 1 0.12 Liechtensteiner 1 0.12 Czech 1 0.12

nationality driver_count British 165 American 158 Italian 99 French 73 German 50 Brazilian 32 Argentine 24 Swiss 23 South African 23 Belgian 23

'\nNationality Analysis:\n1. Counted the number of drivers from each nationality\n2. Calculated what percentage of total F1 drivers each nationality represents\n3. Identified the most common nationality in Formula 1 history\n4. This analysis helps understand which countries have contributed the most drivers to F1\n'